In [3]:
import json
import numpy as np
import pandas as pd
import requests

base_url = 'https://fantasy.premierleague.com/api'

In [26]:
bootstraps = requests.get(base_url + '/bootstrap-static/').json()


In [51]:
bootstraps

{'events': [{'id': 1,
   'name': 'Gameweek 1',
   'deadline_time': '2023-08-11T17:30:00Z',
   'release_time': None,
   'average_entry_score': 64,
   'finished': True,
   'data_checked': True,
   'highest_scoring_entry': 3383750,
   'deadline_time_epoch': 1691775000,
   'deadline_time_game_offset': 0,
   'highest_score': 127,
   'is_previous': False,
   'is_current': False,
   'is_next': False,
   'cup_leagues_created': False,
   'h2h_ko_matches_created': False,
   'ranked_count': 0,
   'chip_plays': [{'chip_name': 'bboost', 'num_played': 163222},
    {'chip_name': '3xc', 'num_played': 287198}],
   'most_selected': 355,
   'most_transferred_in': 1,
   'top_element': 395,
   'top_element_info': {'id': 395, 'points': 14},
   'transfers_made': 0,
   'most_captained': 355,
   'most_vice_captained': 19},
  {'id': 2,
   'name': 'Gameweek 2',
   'deadline_time': '2023-08-18T17:15:00Z',
   'release_time': None,
   'average_entry_score': 44,
   'finished': True,
   'data_checked': True,
   'high

In [36]:
# Get team ids
teams = []
for team in  bootstraps['teams']:
    teams.append({'team_id': team['id'], 'team_name' : team['name'], 'short_name' : team['short_name'], })
team_pd = pd.DataFrame(teams)

team_pd.to_csv('./FG/teams.csv')


In [60]:
# Get positions
positions = []

for position in bootstraps['element_types']:
    positions.append({'id':position['id'], 'plural_name': position['plural_name'], 'plural_name_short': position['plural_name_short'], 'singular_name': position['singular_name'], 'singular_name_short': position['singular_name_short'], 'element_count': position['element_count']})

positions_pd = pd.DataFrame(positions)


players_pd.to_csv('./FG/positions.csv')


In [104]:
# Get player ids
players = []

for player in bootstraps['elements']:
    player_position = None
    player_team = None

    for position in bootstraps['element_types']:
        if(position['id'] == player['element_type']):
            player_position = position['plural_name_short']

    for team in bootstraps['teams']:
        if(team['id'] == player['team']):
            player_team = team['name']
    players.append({'player_id': player['id'], 'first_name': player['first_name'], 'second_name': player['second_name'], 'position_id': player['element_type'], 'position': player_position, 'team_id': player['team'], 'team': player_team, 'team_code': player['team_code'], 'web_name': player['web_name']})
players_pd = pd.DataFrame(players)

players_pd = players_pd.set_index('player_id')


players_pd.to_csv('./FG/players.csv')

In [103]:
player_details = pd.read_csv('./FG/players.csv', index_col='player_id')
player_details

first_name           second_name  position_id position  team_id  \
player_id                                                                   
1            Folarin               Balogun            4      FWD        1   
2             Cédric          Alves Soares            2      DEF        1   
3            Mohamed                Elneny            3      MID        1   
4              Fábio       Ferreira Vieira            3      MID        1   
5            Gabriel  dos Santos Magalhães            2      DEF        1   
...              ...                   ...          ...      ...      ...   
800             Noha                Lemina            3      MID       20   
832           Wesley               Okoduwa            2      DEF       20   
836             Leon               Chiwome            4      FWD       20   
840         Fletcher                Holman            4      FWD       20   
853           Temple              Ojinnaka            3      MID       20   

              team  team_code      web_name  
player_id                                    
1          Arsenal          3       Balogun  
2          Arsenal          3        Cédric  
3          Arsenal          3      M.Elneny  
4          Arsenal          3  Fábio Vieira  
5          Arsenal          3       Gabriel  
...            ...        ...           ...  
800         Wolves         39      N.Lemina  
832         Wolves         39       Okoduwa  
836         Wolves         39       Chiwome  
840         Wolves         39        Holman  
853         Wolves         39      Ojinnaka  

[865 rows x 8 columns]

In [4]:
fg_data = []
with open('./FG/fantasyGO_data.json') as data_file:
    fg_data = json.load(data_file)


In [15]:
details = []
gw_ = 1
for gw in fg_data:
    pages = list(gw.keys())[6:-1]
    for page in pages:
        page_ = gw[page]
        for manager in page_:
            picks = tuple([(player['player_name'], player['points']) for player in manager['pick']])
            manager_details = {'gw': gw_, 'manager': manager['manager'], 'entry': manager['entry'], 'points': float(manager['points'][0:-7]), 'picks': picks}

            details.append(manager_details)
            print(manager_details)
    gw_ += 1


{'gw': 1, 'manager': 'Radynster', 'entry': '1', 'points': 81.5, 'picks': (('Sanchez', '2'), ('Veltman', '1'), ('Wan-Bissaka', '12'), ('Estupiñan', '7'), ('Mitoma', '5'), ('Souček', '7'), ('Ndombele', '0'), ('Eze', '3'), ('João Pedro', '10.5'), ('Haaland', '26'), ('Nketiah', '8'))}
{'gw': 1, 'manager': 'paradise-prince', 'entry': '2', 'points': 79.5, 'picks': (('Steele', '2'), ('Holgate', '0'), ('Wan-Bissaka', '12'), ('Botman', '5'), ('Rodrigo', '13'), ('Garnacho', '3'), ('Mount', '4.5'), ('Enzo', '1'), ('Haaland', '26'), ('J.Alvarez', '5'), ('Nketiah', '8'))}
{'gw': 1, 'manager': 'KloppinSquad 2.0', 'entry': '1', 'points': 77.5, 'picks': (('Steele', '2'), ('Estupiñan', '7'), ('Wan-Bissaka', '12'), ('Gabriel', '1.5'), ('Akanji', '6'), ('Rodrigo', '13'), ('Enciso', '1'), ('Chukwuemeka', '1'), ('Martinelli', '5'), ('Kovačić', '3'), ('Haaland', '26'))}
{'gw': 1, 'manager': 'zbongo', 'entry': '1', 'points': 77.5, 'picks': (('Forster', '0'), ('Dunk', '2'), ('Veltman', '1'), ('Guéhi', '6'), (

In [18]:
managers_pd = pd.DataFrame(details)

managers_pd.to_csv('./FG/managers.csv')